In [ ]:
pip install evaluate mauve-text bert_score

## Evaluate all Generations

In [ ]:
# Import libraries 
import os
import pandas as pd
import re
import numpy as np
from tqdm import tqdm
from evaluate import load
from mauve import compute_mauve

# Load bertscore and bleu
bleu = load("bleu")
bert = load("bertscore")

def evaluate_folder(folder_path):
    # Create a new folder for evaluated dataframes
    output_folder = os.path.join(folder_path, "evaluation")
    os.makedirs(output_folder, exist_ok=True)

    # Iterate over CSV files in the specified folder
    for filename in os.listdir(folder_path):
        if filename.endswith(".csv"):
            print(f"Evaluating DataFrame in file: {filename}")
            # Load dataframe
            df = pd.read_csv(os.path.join(folder_path, filename))

            # Perform evaluation
            df_evaluated = process_dataframe(df)

            # Save evaluated dataframe to new folder
            output_filename = filename.replace(".csv", "_evaluated.csv")
            output_path = os.path.join(output_folder, output_filename)
            df_evaluated.to_csv(output_path, index=False)
            print(f"Evaluated dataframe saved to: {output_path}")

def process_dataframe(df):
    # Remove speaker tags from reference texts
    df['adult_feedback_response'] = df['adult_feedback_response'].apply(lambda x: re.sub(r'^[A-Za-z]:\s*', '', x))

    # add new columns to samples dataframe
    df['bleu_score'] = np.nan
    df['bleu_brevity_penalty'] = np.nan
    df['bleu_length_ratio'] = np.nan
    df['mauve_score'] = np.nan

    # there will be a bertf1 for each model response
    for i in range(1,6):
        df[f'bert_f1_r{i}'] = np.nan

    # construct pairs dataframe
    print('Constructing pairs dataframe...')
    pairs = pd.DataFrame(columns=['generated_response', 'human_response', 'sample_number'])

    for sample_number, row in tqdm(df.iterrows(), total=len(df)):
        human_response = row['adult_feedback_response']
        model_responses = [row[f"generated_response_{i}"] for i in range(1,6)]
        for model_response_idx,model_response in enumerate(model_responses, start=1):
            pairs = pd.concat([pairs, pd.DataFrame({
                    'generated_response': [model_response],
                    'human_response': [human_response],
                    'sample_number': [sample_number],
                    'model_response_index': [model_response_idx],
                })])
    pairs = pairs.reset_index(drop=True)
    print(f'Number of pairs: {len(pairs)}')

    # compute bleu
    print('Computing BLEU score...')
    bleu_results = bleu.compute(
        predictions=pairs['generated_response'].values,
        references=pairs['human_response'].values)
    print("Done.")
    bleu_score = bleu_results['bleu']
    bleu_brevity_penalty = bleu_results['brevity_penalty']
    bleu_length_ratio = bleu_results['length_ratio']
    print(f"BLEU score: {bleu_score}")
    print(f"Brevity penalty: {bleu_brevity_penalty}")
    print(f"Length ratio: {bleu_length_ratio}")
    # add to pairs dataframe
    pairs['bleu_score'] = [bleu_score] * len(pairs)
    pairs['bleu_brevity_penalty'] = [bleu_brevity_penalty] * len(pairs)
    pairs['bleu_length_ratio'] = [bleu_length_ratio] * len(pairs)

    # compute mauve
    print('Computing MAUVE score...')
    mauve_results = compute_mauve(
            p_text=pairs['generated_response'].values,
            q_text=pairs['human_response'].values,
            device_id=0,  # use GPU 0 for featurization
            max_text_length=256,  # truncate text to x token
            featurize_model_name='gpt2-large',
        )
    mauve_score = mauve_results.mauve
    print(f'MAUVE score: {mauve_score}')
    print('Done.')
    # add to pairs dataframe
    pairs['mauve_score'] = [mauve_score] * len(pairs)

    print('Computing BERT score...')
    bert_results = bert.compute(
            predictions=pairs['generated_response'].values,
            references=pairs['human_response'].values,
            model_type="bert-base-uncased",
            use_fast_tokenizer=True,
            verbose=True)
    mean_bert_f1 = np.mean(bert_results['f1'])
    n_bert_f1s = len(bert_results['f1'])
    bert_f1s = bert_results['f1']
    print(f"Mean BERT F1 score: {mean_bert_f1}")
    print(f"Number of BERT F1 scores: {n_bert_f1s}")
    print("Done.")
    # add to pairs dataframe
    pairs['bert_f1'] = bert_f1s

    # add scores to samples dataframe
    print('Adding scores to samples dataframe...')
    for _, pair in tqdm(pairs.iterrows(), total=len(pairs)):
        sample_idx = pair['sample_number']
        model_response_idx = str(int(pair['model_response_index']))
        df.at[sample_idx, 'bleu_score'] = pair['bleu_score']
        df.at[sample_idx, 'bleu_brevity_penalty'] = pair['bleu_brevity_penalty']
        df.at[sample_idx, 'bleu_length_ratio'] = pair['bleu_length_ratio']
        df.at[sample_idx, 'mauve_score'] = pair['mauve_score']
        df.at[sample_idx, f'bert_f1_r{model_response_idx}'] = pair['bert_f1']
    print('Done.')
    return df

# Provide the folder path containing CSV files for evaluation
folder_path = '/content/drive/MyDrive/generated_responses'
evaluate_folder(folder_path)

Evaluating DataFrame in file: opt_rephrase_generated_responses.csv
Constructing pairs dataframe...


100%|██████████| 69/69 [00:00<00:00, 247.28it/s]


Number of pairs: 345
Computing BLEU score...
Done.
BLEU score: 0.04918416937721405
Brevity penalty: 1.0
Length ratio: 1.2221574344023323
Computing MAUVE score...


tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/666 [00:00<?, ?B/s]

...

computing greedy matching.


  0%|          | 0/6 [00:00<?, ?it/s]

done in 4129.10 seconds, 0.08 sentences/sec
Mean BERT F1 score: 0.4431599823029145
Number of BERT F1 scores: 345
Done.
Adding scores to samples dataframe...


100%|██████████| 345/345 [00:00<00:00, 5799.09it/s]

Done.
Evaluated dataframe saved to: /content/drive/MyDrive/generated_responses/evaluation/dialogpt_base_rephrase_generated_responses_evaluated.csv
